In [1]:
from astropy.io import fits
import numpy as np
from astropy.table import QTable,vstack
import astropy.units as u
import astropy.utils
from astropy.coordinates import SkyCoord
import matplotlib.pyplot as plt
import matplotlib.colors
from scipy.stats import chisquare
from scipy.stats import chi2
from scipy.stats import lognorm
from astropy.timeseries import LombScargle
import time
from astropy.visualization import hist
from scipy.optimize import curve_fit
from astropy.timeseries import BoxLeastSquares
from astropy.timeseries import TimeSeries
from astropy.time import Time
import functions
import upsilon
from tqdm import tqdm

-------------------------------
* WARNING: No pyFFTW detected *
-------------------------------


In [3]:
t=QTable.read('t_ZTF_matched_1arcsec.csv')

In [8]:
t=t['GroupID','filtercode','oid','ra','dec','ngoodobsrel']

In [12]:
t.rename_column('GroupID', 'SourceID')
t.rename_column('filtercode', 'filter')
t.rename_column('oid', 'OID')
t.rename_column('ngoodobsrel', 'numobs')
t.rename_column('ra', 'RA')
t.rename_column('dec', 'DEC')

In [17]:
t_zr=t[t['filter']=='zr']
t_zg=t[t['filter']=='zg']

In [24]:
t_zr.write('t_zr_raw.ecsv')
t_zg.write('t_zg_raw.ecsv')

In [6]:
def constant_fit(x,a):
    return a

# Load a classification model.
rf_model = upsilon.load_rf_model()

error_zr=[]
t=QTable.read('t_zr_raw.ecsv')

t.add_column(np.zeros(len(t)),name='DELTA_SIG_MAG',index=-1)
t.add_column(np.zeros(len(t)),name='CONST_CHI2',index=-1)
t.add_column(np.zeros(len(t)),name='LNP_SIG',index=-1)
t.add_column(np.zeros(len(t)),name='period',index=-1)
t.add_column(np.zeros(len(t)),name='period_c',index=-1)
t.add_column(np.zeros(len(t)),name='power',index=-1)
t.add_column(np.zeros(len(t)),name='power_c',index=-1)

t.add_column(np.empty(len(t),'S14'),name='upsilon_class',index=-1)
t.add_column(np.zeros(len(t)),name='upsilon_prob',index=-1)
t.add_column(np.zeros(len(t)),name='upsilon_flag',index=-1)
t.add_column(np.zeros(len(t)),name='upsilon_period',index=-1)


for i,row in tqdm(enumerate(t),total=len(t)):
    ID_str=str(int(row['OID']))
    try:
        t_ZTF=QTable.read('https://irsa.ipac.caltech.edu/cgi-bin/ZTF/nph_light_curves?ID='+ID_str)
    except:
        print('2nd download attempt in 30 seconds...')
        time.sleep(30)
        try:
            t_ZTF=QTable.read('https://irsa.ipac.caltech.edu/cgi-bin/ZTF/nph_light_curves?ID='+ID_str)
        except:
            print('3rd download attempt in 30 seconds...')
            time.sleep(30)
            try:
                t_ZTF=QTable.read('https://irsa.ipac.caltech.edu/cgi-bin/ZTF/nph_light_curves?ID='+ID_str)
            except:
                print('last attempt failed, saving the index to error_zr')
                error_zr.append(i)
    
    t_ZTF=t_ZTF[(t_ZTF['mjd']<58481*u.day)|(t_ZTF['mjd']>58482*u.day)]
    t_ZTF=t_ZTF[(t_ZTF['mjd']<58472*u.day)|(t_ZTF['mjd']>58474*u.day)]
    t_ZTF=t_ZTF[(t_ZTF['mjd']<59032*u.day)|(t_ZTF['mjd']>59033*u.day)]
    
    
    if len(t_ZTF)<10:
        t[i]['DELTA_SIG_MAG']=np.nan
        t[i]['CONST_CHI2']=np.nan
        t[i]['LNP_SIG']=np.nan
        t[i]['period']=np.nan
        t[i]['period_c']=np.nan
        t[i]['power']=np.nan
        t[i]['power_c']=np.nan
        t[i]['upsilon_class']=np.nan
        t[i]['upsilon_prob']=np.nan
        t[i]['upsilon_flag']=np.nan
        t[i]['upsilon_period']=np.nan

        print('This guy has too few observations')
    else:
        DELTA_SIG_MAG=(t_ZTF['mag'].max()-t_ZTF['mag'].min())/(t_ZTF['magerr'][t_ZTF['mag'].argmax()]**2+t_ZTF['magerr'][t_ZTF['mag'].argmin()]**2)

        popt, pcov = curve_fit(constant_fit,t_ZTF['mjd'],t_ZTF['mag'],sigma=t_ZTF['magerr'])
        CONST_CHI2=(((t_ZTF['mag'].value-popt)**2)/(t_ZTF['magerr'].value**2)).sum()/(len(t_ZTF)-1)
        
        ls = LombScargle(t_ZTF['mjd'],t_ZTF['mag'], t_ZTF['magerr'])
        try:
            freq, power = ls.autopower(nyquist_factor=300,minimum_frequency=1/(600*u.day),maximum_frequency=1/(0.1*u.day))
            LNP_SIG=ls.false_alarm_probability(power.max())
            period=(1./freq[power.argmax()]).value
            powermax=power.max().value
            powermax_ind=power.argmax()
        except:
            LNP_SIG=np.nan
            period=np.nan
            powermax=np.nan
            powermax_ind=np.nan
            
        con_mag=np.zeros(t_ZTF['mag'].shape)+t_ZTF['mag'].mean()
        con_err=np.zeros(t_ZTF['magerr'].shape)+t_ZTF['magerr'].mean()
        ls = LombScargle(t_ZTF['mjd'],con_mag, con_err,fit_mean=False, center_data=False)
        try:
            freq, power = ls.autopower(nyquist_factor=300,minimum_frequency=1/(600*u.day),maximum_frequency=1/(0.1*u.day))
            period_1=(1./freq[power.argmax()]).value
            if np.isnan(powermax_ind):
                powermax_c=np.nan
            else:
                powermax_c=power[powermax_ind].value
        except:
            period_1=np.nan
            powermax_c=np.nan
            
        t[i]['DELTA_SIG_MAG']=DELTA_SIG_MAG.value
        t[i]['CONST_CHI2']=CONST_CHI2
        t[i]['LNP_SIG']=LNP_SIG
        t[i]['period']=period
        t[i]['period_c']=period_1
        t[i]['power']=powermax
        t[i]['power_c']=powermax_c
    
        try:
            # Extract features (date,mag,magerr)
            e_features = upsilon.ExtractFeatures(np.array(t_ZTF['mjd']),np.array(t_ZTF['mag']),np.array(t_ZTF['magerr']))
            e_features.run()
            features = e_features.get_features()
    
            # Classify the light curve
            label, probability, flag = upsilon.predict(rf_model, features)
            # label, probability, flag,features['period']
    
            t[i]['upsilon_class']=label
            t[i]['upsilon_prob']=probability
            t[i]['upsilon_flag']=flag
            t[i]['upsilon_period']=features['period']
        except:
            t[i]['upsilon_class']=np.nan
            t[i]['upsilon_prob']=np.nan
            t[i]['upsilon_flag']=np.nan
            t[i]['upsilon_period']=np.nan
            
    #_=input('no bug!')

    

t.write('t_zr_0418.ecsv')
print('Hooray! Done zr!')
astropy.utils.data.clear_download_cache()

D:\Anaconda3\lib\site-packages\sklearn\base.py:329: UserWarning: Trying to unpickle estimator DecisionTreeClassifier from version 0.24.1 when using version 1.0.2. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/modules/model_persistence.html#security-maintainability-limitations
  warnings.warn(
D:\Anaconda3\lib\site-packages\sklearn\base.py:329: UserWarning: Trying to unpickle estimator RandomForestClassifier from version 0.24.1 when using version 1.0.2. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/modules/model_persistence.html#security-maintainability-limitations
  warnings.warn(
  0%|                                                                             | 2/12161 [01:05<92:59:20, 27.53s/it]D:\Anaconda3\lib\site-packages\upsilon\extract_features\extract_features.py:60: UserWarning: The number of da

This guy has too few observations


  0%|                                                                             | 9/12161 [02:21<24:57:00,  7.39s/it]

This guy has too few observations


D:\Anaconda3\lib\site-packages\upsilon\extract_features\extract_features.py:60: UserWarning: The number of data points are less than 80.
  warnings.warn('The number of data points are less than %d.'
  0%|                                                                            | 10/12161 [02:24<20:00:51,  5.93s/it]D:\Anaconda3\lib\site-packages\upsilon\extract_features\extract_features.py:60: UserWarning: The number of data points are less than 80.
  warnings.warn('The number of data points are less than %d.'
  0%|                                                                            | 11/12161 [02:27<17:36:39,  5.22s/it]D:\Anaconda3\lib\site-packages\upsilon\extract_features\extract_features.py:60: UserWarning: The number of data points are less than 80.
  warnings.warn('The number of data points are less than %d.'
  0%|                                                                            | 13/12161 [02:31<11:40:24,  3.46s/it]

...

100%|████████████████████████████████████████████████████████████████████████▊| 12140/12161 [25:27:59<03:55, 11.21s/it]

This guy has too few observations


100%|████████████████████████████████████████████████████████████████████████▉| 12142/12161 [25:29:44<09:27, 29.88s/it]D:\Anaconda3\lib\site-packages\upsilon\extract_features\extract_features.py:60: UserWarning: The number of data points are less than 80.
  warnings.warn('The number of data points are less than %d.'
100%|████████████████████████████████████████████████████████████████████████▉| 12148/12161 [25:32:15<06:20, 29.23s/it]D:\Anaconda3\lib\site-packages\upsilon\extract_features\extract_features.py:60: UserWarning: The number of data points are less than 80.
  warnings.warn('The number of data points are less than %d.'
100%|████████████████████████████████████████████████████████████████████████▉| 12150/12161 [25:32:22<02:57, 16.11s/it]D:\Anaconda3\lib\site-packages\upsilon\extract_features\extract_features.py:60: UserWarning: The number of data points are less than 80.
  warnings.warn('The number of data points are less than %d.'
100%|█████████████████████████████████████████

This guy has too few observations


Hooray! Done zr!


In [7]:
def constant_fit(x,a):
    return a

# Load a classification model.
rf_model = upsilon.load_rf_model()

error_zr=[]
t=QTable.read('t_zg_raw.ecsv')

t.add_column(np.zeros(len(t)),name='DELTA_SIG_MAG',index=-1)
t.add_column(np.zeros(len(t)),name='CONST_CHI2',index=-1)
t.add_column(np.zeros(len(t)),name='LNP_SIG',index=-1)
t.add_column(np.zeros(len(t)),name='period',index=-1)
t.add_column(np.zeros(len(t)),name='period_c',index=-1)
t.add_column(np.zeros(len(t)),name='power',index=-1)
t.add_column(np.zeros(len(t)),name='power_c',index=-1)

t.add_column(np.empty(len(t),'S14'),name='upsilon_class',index=-1)
t.add_column(np.zeros(len(t)),name='upsilon_prob',index=-1)
t.add_column(np.zeros(len(t)),name='upsilon_flag',index=-1)
t.add_column(np.zeros(len(t)),name='upsilon_period',index=-1)


for i,row in tqdm(enumerate(t),total=len(t)):
    ID_str=str(int(row['OID']))
    try:
        t_ZTF=QTable.read('https://irsa.ipac.caltech.edu/cgi-bin/ZTF/nph_light_curves?ID='+ID_str)
    except:
        print('2nd download attempt in 30 seconds...')
        time.sleep(30)
        try:
            t_ZTF=QTable.read('https://irsa.ipac.caltech.edu/cgi-bin/ZTF/nph_light_curves?ID='+ID_str)
        except:
            print('3rd download attempt in 30 seconds...')
            time.sleep(30)
            try:
                t_ZTF=QTable.read('https://irsa.ipac.caltech.edu/cgi-bin/ZTF/nph_light_curves?ID='+ID_str)
            except:
                print('last attempt failed, saving the index to error_zr')
                error_zr.append(i)
    
    
    if len(t_ZTF)<10:
        t[i]['DELTA_SIG_MAG']=np.nan
        t[i]['CONST_CHI2']=np.nan
        t[i]['LNP_SIG']=np.nan
        t[i]['period']=np.nan
        t[i]['period_c']=np.nan
        t[i]['power']=np.nan
        t[i]['power_c']=np.nan
        t[i]['upsilon_class']=np.nan
        t[i]['upsilon_prob']=np.nan
        t[i]['upsilon_flag']=np.nan
        t[i]['upsilon_period']=np.nan

        print('This guy has too few observations')
    else:
        DELTA_SIG_MAG=(t_ZTF['mag'].max()-t_ZTF['mag'].min())/(t_ZTF['magerr'][t_ZTF['mag'].argmax()]**2+t_ZTF['magerr'][t_ZTF['mag'].argmin()]**2)

        popt, pcov = curve_fit(constant_fit,t_ZTF['mjd'],t_ZTF['mag'],sigma=t_ZTF['magerr'])
        CONST_CHI2=(((t_ZTF['mag'].value-popt)**2)/(t_ZTF['magerr'].value**2)).sum()/(len(t_ZTF)-1)
        
        ls = LombScargle(t_ZTF['mjd'],t_ZTF['mag'], t_ZTF['magerr'])
        try:
            freq, power = ls.autopower(nyquist_factor=300,minimum_frequency=1/(600*u.day),maximum_frequency=1/(0.1*u.day))
            LNP_SIG=ls.false_alarm_probability(power.max())
            period=(1./freq[power.argmax()]).value
            powermax=power.max().value
            powermax_ind=power.argmax()
        except:
            LNP_SIG=np.nan
            period=np.nan
            powermax=np.nan
            powermax_ind=np.nan
            
        con_mag=np.zeros(t_ZTF['mag'].shape)+t_ZTF['mag'].mean()
        con_err=np.zeros(t_ZTF['magerr'].shape)+t_ZTF['magerr'].mean()
        ls = LombScargle(t_ZTF['mjd'],con_mag, con_err,fit_mean=False, center_data=False)
        try:
            freq, power = ls.autopower(nyquist_factor=300,minimum_frequency=1/(600*u.day),maximum_frequency=1/(0.1*u.day))
            period_1=(1./freq[power.argmax()]).value
            if np.isnan(powermax_ind):
                powermax_c=np.nan
            else:
                powermax_c=power[powermax_ind].value
        except:
            period_1=np.nan
            powermax_c=np.nan
            
        t[i]['DELTA_SIG_MAG']=DELTA_SIG_MAG.value
        t[i]['CONST_CHI2']=CONST_CHI2
        t[i]['LNP_SIG']=LNP_SIG
        t[i]['period']=period
        t[i]['period_c']=period_1
        t[i]['power']=powermax
        t[i]['power_c']=powermax_c
    
        try:
            # Extract features (date,mag,magerr)
            e_features = upsilon.ExtractFeatures(np.array(t_ZTF['mjd']),np.array(t_ZTF['mag']),np.array(t_ZTF['magerr']))
            e_features.run()
            features = e_features.get_features()
    
            # Classify the light curve
            label, probability, flag = upsilon.predict(rf_model, features)
            # label, probability, flag,features['period']
    
            t[i]['upsilon_class']=label
            t[i]['upsilon_prob']=probability
            t[i]['upsilon_flag']=flag
            t[i]['upsilon_period']=features['period']
        except:
            t[i]['upsilon_class']=np.nan
            t[i]['upsilon_prob']=np.nan
            t[i]['upsilon_flag']=np.nan
            t[i]['upsilon_period']=np.nan
            
    #_=input('no bug!')

    

t.write('t_zg_0418.ecsv')
print('Hooray! Done zg!')
astropy.utils.data.clear_download_cache()

D:\Anaconda3\lib\site-packages\sklearn\base.py:329: UserWarning: Trying to unpickle estimator DecisionTreeClassifier from version 0.24.1 when using version 1.0.2. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/modules/model_persistence.html#security-maintainability-limitations
  warnings.warn(
D:\Anaconda3\lib\site-packages\sklearn\base.py:329: UserWarning: Trying to unpickle estimator RandomForestClassifier from version 0.24.1 when using version 1.0.2. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/modules/model_persistence.html#security-maintainability-limitations
  warnings.warn(
  0%|                                                                              | 1/7861 [00:06<14:50:02,  6.79s/it]D:\Anaconda3\lib\site-packages\upsilon\extract_features\extract_features.py:60: UserWarning: The number of da

This guy has too few observations


  0%|                                                                               | 4/7861 [00:16<7:49:31,  3.59s/it]D:\Anaconda3\lib\site-packages\upsilon\extract_features\extract_features.py:60: UserWarning: The number of data points are less than 80.
  warnings.warn('The number of data points are less than %d.'
  0%|                                                                               | 5/7861 [00:17<6:20:33,  2.91s/it]D:\Anaconda3\lib\site-packages\upsilon\extract_features\extract_features.py:60: UserWarning: The number of data points are less than 80.
  warnings.warn('The number of data points are less than %d.'
  0%|                                                                              | 8/7861 [00:38<11:43:41,  5.38s/it]

This guy has too few observations


  0%|                                                                               | 9/7861 [00:39<9:07:57,  4.19s/it]

...

100%|██████████████████████████████████████████████████████████████████████████▉| 7859/7861 [10:58:06<00:09,  4.69s/it]

This guy has too few observations


D:\Anaconda3\lib\site-packages\upsilon\extract_features\extract_features.py:60: UserWarning: The number of data points are less than 80.
  warnings.warn('The number of data points are less than %d.'
100%|███████████████████████████████████████████████████████████████████████████| 7861/7861 [10:58:11<00:00,  5.02s/it]

This guy has too few observations


Hooray! Done zg!
